In [1]:
import json
import time
import math
import os
import numpy as np
import keras
import keras.backend as K
from keras.layers import Dense, Input, Conv1D, Flatten, BatchNormalization, LeakyReLU, ReLU, Dropout
from keras.optimizers import Adam
from keras.utils import plot_model
from keras.models import Model
from keras.regularizers import l1, l2
from keras.callbacks import EarlyStopping
import tensorflow as tf
from sklearn.utils import class_weight
import skopt
from skopt import gp_minimize
from skopt.space import Real, Integer, Categorical
from skopt.utils import use_named_args

import matplotlib.pyplot as plt

%matplotlib inline 

Using TensorFlow backend.
/home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


In [2]:
class Data():
    
    def __init__(self, fp):
        
        self.fp = fp
        self.load_data()
        self.shuffle()
        self.get_sample_weights()
        
    def load_data(self):
        start = time.time()
        try:
            self.x = x
            self.y = y
        except:
            with open('{}.json'.format(self.fp), 'r') as file:
                temp = json.load(file)
            self.x = np.array([np.array(vec) for vec in temp['x']])
            self.y = np.array(temp['y'])
        print('X shape: {}'.format(self.x.shape))
        print('Y shape: {}'.format(self.y.shape))
        
    def get_sample_weights(self):
        weight_dic = {0: np.sum(self.y)/self.y.shape[0]/np.sum(1-self.y)}
        weight_dic[1] = (1-weight_dic[0])/np.sum(self.y)
        self.weights = np.array([weight_dic[self.y[index]] for index in range(self.y.shape[0])])
        
    def shuffle(self):
        temp_x = np.zeros(self.x.shape)
        temp_y = np.zeros(self.y.shape)
        m = self.y.shape[0]
        index = np.arange(m)
        np.random.shuffle(index)
        for x in range(m):
            value = int(index[int(x)])
            temp_x[x,:] = self.x[value,:]
            temp_y[x] = self.y[index[int(x)]]
        self.x = temp_x
        self.y = temp_y

In [3]:
class DenseModel():
    
    def __init__(
        self,
        input_shape=None,
        layers=None,
        regularizer=None,
        advanced_activation=None,
        activation='relu',
        dropout=0,
        experiment_number=None,
        lr = 0.001
    ):
        
        self.input_shape = input_shape[1]
        self.layers = layers
        self.regularizer = regularizer
        self.advanced_activation = advanced_activation
        self.activation = activation
        self.dropout = dropout
        self.early_stopping = [EarlyStopping(monitor=parameter, patience=10) for parameter in ['val_loss', 'val_acc']]
        self.experiment_number = experiment_number
        self.lr = lr
        
        self.build_model()
        self.create_experimiment_directory()
        
    def build_model(self):
        inputs = Input(shape=(self.input_shape,))
        for dim in self.layers:
            try:
                net = Dense(dim, activation=self.activation, kernel_regularizer=self.regularizer)(net)
                if self.advanced_activation is not None:
                    net = self.advanced_activation()(net)
                #net = BatchNormalization()(net)
                net = Dropout(self.dropout)(net)
            except:
                net = Dense(dim, activation=self.activation, kernel_regularizer=self.regularizer)(inputs)
                if self.advanced_activation is not None:
                    net = self.advanced_activation()(net)
                #net = BatchNormalization()(net)
                net = Dropout(self.dropout)(net)
        outputs = Dense(1, activation='sigmoid')(net)
        self.model = Model(inputs=inputs, outputs=outputs)
        self.model.compile(Adam(lr=self.lr), loss='binary_crossentropy', metrics=['accuracy', precision, recall, f_one])
        
        
    def create_experimiment_directory(self):
        if self.experiment_number is None:
            print('creating ner experiment directory')
            self.experiment_number = len([file for file in os.listdir(os.getcwd()) if '_' in file and file.split('_')[0] == 'experiment'])
        self.experiment_dir = os.getcwd() + '/experiment_{}/'.format(self.experiment_number)
        if not os.path.exists(self.experiment_dir):
            os.mkdir(self.experiment_dir)
        
        
        
    def save_model(self, model_dic):
        model_number = list(model_dic.keys())[0]
        model, history, fp_type = model_dic[model_number]
        save_dic = {
            'history': history.history,
            'num_layers': len(model.layers),
            'layer_size': model.layers[-0],
            'dropout': model.dropout,
            'regularizer': str(type(model.regularizer)),
            'activation': str(type(model.activation()))
        }
        file_name = '{}_train_history.json'.format(model_number)
        with open(self.experiment_dir+file_name, 'w') as file:
            json.dump(save_dic, file)

In [4]:
def precision(y_true, y_pred):
    true_pos = calc_true_pos(y_true, y_pred)
    return true_pos/tf.reduce_sum(y_pred)

def recall(y_true, y_pred):
    true_pos = calc_true_pos(y_true, y_pred)
    return true_pos/tf.reduce_sum(y_true)

def f_one(y_true, y_pred):
    prec = precision(y_true, y_pred)
    rec = recall(y_true, y_pred)
    return 2*prec*rec/(prec+rec)
    
def calc_true_pos(y_true, y_pred):
    return tf.reduce_sum(y_true*y_pred)

def calc_true_negative(y_true, y_pred):
    return tf.reduce_sum((1-y_true)*(1-y_pred))

def calc_false_positive(y_true, y_pred):
    return tf.reduce_sum((1-y_true)*y_pred)

def calc_false_negative(y_true, y_pred):
    return tf.reduce_sum(y_true*(1-y_pred))

def calc_roc(y_true, predictions, threshold):
    y_pred = 1*(predictions>=threshold)
    false_positive = calc_false_positive(y_true, y_pred)
    true_negative = calc_true_negative(y_true, y_pred)
    true_positive = calc_true_positive(y_true, y_pred)
    false_negative = calc_false_negative(y_true, y_pred)
    false_positive_rate = false_positive/(false_positive+true_negative) # x-axis
    true_positive_rate = true_positive/(true_positive+false_negative) # y-axis
    return (false_positive_rate, true_positive_rate)

def roc_curve(y_true, predictions, num_steps, title=None):
    false_positive_list = []
    true_positive_list = []
    for step in range(0, num_steps+2):
        false_positive_rate, true_positive_rate = calc_roc(y_true, predictions, step/num_steps)
        false_positive_list.append(false_positive_rate)
        true_positive_list.append(true_positive_rate)
    plot = plot_curve(false_positive_list, true_positive_list, title=title)
    return plot

def plot_curve(x_values, y_values, title=None):
    fig = plt.figure()
    ax = plt.axes()
    plt.plot(x_values, y_values)
    plt.plot([x/1000 for x in range(1000)], [x/1000 for x in range(1000)])
    if title is not None:
        plt.title(title)
    return plt

In [5]:
number_layers = Integer(low=1, high=5, name='number_layers')
layer_size = Integer(low=5, high=11, name='layer_size')
alpha = Integer(low=0, high=10, name='alpha')
dropout = Real(low=0, high=1, name='dropout')
learning_rate = Integer(low=1, high=6, name='learning_rate')
regularizer = Categorical(['l1', 'l2'], name='regularizer')
activation = Categorical(['sigmoid', 'relu', 'leaky_relu', 'tanh'], name='activation')

dimensions = [number_layers, layer_size, alpha, dropout, learning_rate, regularizer, activation]
default_parameters = [1, 5, 0, 0, 1, 'l2', 'relu']

In [6]:
@use_named_args(dimensions=dimensions)
def fitness(number_layers, layer_size, alpha, dropout, learning_rate, regularizer, activation):
    layers = [2**layer_size]*number_layers
    alpha = 1/10**alpha
    learning_rate = 1/10**learning_rate
    regularizer_dic = {'l1': l1, 'l2': l2}
    advanced_activation_dic = {'sigmoid': None, 'relu': None, 'leaky_relu': LeakyReLU, 'tanh': None}
    activation_dic = {'sigmoid': 'sigmoid', 'relu': 'relu', 'leaky_relu': None, 'tanh': 'tanh'}
    save_activation = activation
    dropout = round(dropout,2)
    
    dense = DenseModel(
        input_shape = data.x.shape,
        layers = layers,
        regularizer = regularizer_dic[regularizer](alpha),
        advanced_activation = advanced_activation_dic[activation],
        activation = activation_dic[activation],
        dropout = dropout,
        experiment_number = experiment_number,
        lr = learning_rate
    )
    
    dense.model.summary()
    
    history = dense.model.fit(
        x=data.x,
        y=data.y,
        epochs=500,
        batch_size=128,
        validation_split=0.2,
        sample_weight=data.weights,
        callbacks=dense.early_stopping,
        verbose=1
    )
    
    validation_accuracy = -np.max(history.history['val_acc'])
    
    if len([file for file in os.listdir(dense.experiment_dir) if file.split('.')[-1] != 'ipynb_checkpoints']) == 0:
        model_number = 0
    else:
        model_number = len(set([file.split('_')[1] for file in os.listdir(dense.experiment_dir) if '_' in list(file) and file.split('_')[0] == 'model']))
    
    save_dic = {
        'number_layers': int(number_layers),
        'layer_size': int(layer_size),
        'alpha': float(alpha),
        'dropout': float(dropout),
        'learning_rate': float(learning_rate),
        'activation': activation,
        'val_acc': float(-validation_accuracy)
    }
    
    file_name = dense.experiment_dir+'model_' + str(model_number) + '_architecture.json'
    with open(file_name, 'w') as file:
        json.dump(save_dic, file)
       
    # Save plot of learning curve
    fig = plt.figure()
    plt.plot(np.arange(len(history.history['val_loss'])), history.history['val_loss'], label='val_loss')
    plt.plot(np.arange(len(history.history['loss'])), history.history['loss'], label='loss')
    plt.gcf().subplots_adjust(bottom=0.18)
    plt.ylabel('Loss')
    plt.xlabel('Iterations')
    plt.legend(loc='upper right')
    txt_1 = 'Layers: {}, Layer size: {}, Dropout: {}, Learning rate: {}'.format(len(layers), layers[-1], dropout, learning_rate)
    txt_2 = 'Regularization: {}, Alpha: {}, Activaiton: {}'.format(regularizer, alpha, save_activation)
    plt.figtext(0.5, 0.05, txt_1, ha='center', wrap=False)
    plt.figtext(0.5, 0.012, txt_2, ha='center', wrap=False)
    file_name = dense.experiment_dir+'model_' + str(model_number) + '_learning_curve.png'
    plt.savefig(file_name, dpi=400)
    
    return validation_accuracy

In [ ]:
experiment_number = 5
for fp in ['fp2', 'fp3', 'fp4', 'maccs']: 
    data = Data(fp)
    search_result = gp_minimize(
        func = fitness,
        dimensions = dimensions,
        acq_func = 'EI',
        n_calls = 300
    )
    experiment_number += 1

W0920 13:44:17.632120 140401996117824 deprecation_wrapper.py:119] From /home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0920 13:44:17.650911 140401996117824 deprecation_wrapper.py:119] From /home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0920 13:44:17.655134 140401996117824 deprecation_wrapper.py:119] From /home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0920 13:44:17.674536 140401996117824 deprecation_wrapper.py:119] From /home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:133: The name tf.placeholder_with_default is deprecate

X shape: (17201, 312)
Y shape: (17201,)
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 312)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 1024)              320512    
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 1024)              0         
_________________________________________________________________
dropout_1 (Dropout)          (None, 1024)              0         
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 1025      
Total params: 321,537
Trainable params: 321,537
Non-trainable params: 0
_________________________________________________________________
Train on 13760 samples, validate on 3441 samples
Epoch 1/500
13760/13760 [======================

Epoch 11/500
13760/13760 [==============================] - 1s 68us/step - loss: 2.6261e-05 - acc: 0.7994 - precision: 0.6326 - recall: 0.8536 - f_one: 0.7255 - val_loss: 2.4688e-05 - val_acc: 0.8172 - val_precision: 0.6269 - val_recall: 0.8623 - val_f_one: 0.7242
Epoch 12/500
13760/13760 [==============================] - 1s 57us/step - loss: 2.5920e-05 - acc: 0.8047 - precision: 0.6372 - recall: 0.8557 - f_one: 0.7293 - val_loss: 2.4304e-05 - val_acc: 0.8192 - val_precision: 0.6332 - val_recall: 0.8640 - val_f_one: 0.7290
Epoch 13/500
13760/13760 [==============================] - 1s 58us/step - loss: 2.5208e-05 - acc: 0.8134 - precision: 0.6458 - recall: 0.8595 - f_one: 0.7364 - val_loss: 2.4018e-05 - val_acc: 0.8213 - val_precision: 0.6338 - val_recall: 0.8713 - val_f_one: 0.7320
Epoch 14/500
13760/13760 [==============================] - 1s 63us/step - loss: 2.4992e-05 - acc: 0.8172 - precision: 0.6502 - recall: 0.8612 - f_one: 0.7400 - val_loss: 2.3760e-05 - val_acc: 0.8204 - val

13760/13760 [==============================] - 1s 67us/step - loss: 6.3771 - acc: 0.6269 - precision: 0.4447 - recall: 0.4289 - f_one: 0.4354 - val_loss: 6.3235 - val_acc: 0.6353 - val_precision: 0.4375 - val_recall: 0.4312 - val_f_one: 0.4326
Epoch 4/500
13760/13760 [==============================] - 1s 69us/step - loss: 6.2716 - acc: 0.6285 - precision: 0.4442 - recall: 0.4319 - f_one: 0.4370 - val_loss: 6.2184 - val_acc: 0.6379 - val_precision: 0.4369 - val_recall: 0.4340 - val_f_one: 0.4337
Epoch 5/500
13760/13760 [==============================] - 1s 73us/step - loss: 6.1668 - acc: 0.6302 - precision: 0.4439 - recall: 0.4354 - f_one: 0.4385 - val_loss: 6.1140 - val_acc: 0.6417 - val_precision: 0.4363 - val_recall: 0.4368 - val_f_one: 0.4348
Epoch 6/500
13760/13760 [==============================] - 1s 77us/step - loss: 6.0628 - acc: 0.6325 - precision: 0.4430 - recall: 0.4378 - f_one: 0.4391 - val_loss: 6.0104 - val_acc: 0.6460 - val_precision: 0.4358 - val_recall: 0.4395 - val_f_

Epoch 35/500
13760/13760 [==============================] - 1s 66us/step - loss: 3.4338 - acc: 0.6810 - precision: 0.4321 - recall: 0.5034 - f_one: 0.4640 - val_loss: 3.3942 - val_acc: 0.6835 - val_precision: 0.4248 - val_recall: 0.5046 - val_f_one: 0.4593
Epoch 36/500
13760/13760 [==============================] - 1s 62us/step - loss: 3.3560 - acc: 0.6759 - precision: 0.4318 - recall: 0.5056 - f_one: 0.4648 - val_loss: 3.3169 - val_acc: 0.6818 - val_precision: 0.4245 - val_recall: 0.5067 - val_f_one: 0.4600
Epoch 37/500
13760/13760 [==============================] - 1s 71us/step - loss: 3.2792 - acc: 0.6732 - precision: 0.4315 - recall: 0.5079 - f_one: 0.4655 - val_loss: 3.2405 - val_acc: 0.6748 - val_precision: 0.4242 - val_recall: 0.5089 - val_f_one: 0.4608
Epoch 38/500
13760/13760 [==============================] - 1s 68us/step - loss: 3.2032 - acc: 0.6674 - precision: 0.4313 - recall: 0.5100 - f_one: 0.4663 - val_loss: 3.1650 - val_acc: 0.6672 - val_precision: 0.4240 - val_recall:

...

/home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/ipykernel_launcher.py:58: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_768 (InputLayer)       (None, 312)               0         
_________________________________________________________________
dense_3705 (Dense)           (None, 128)               40064     
_________________________________________________________________
dropout_2170 (Dropout)       (None, 128)               0         
_________________________________________________________________
dense_3706 (Dense)           (None, 128)               16512     
_________________________________________________________________
dropout_2171 (Dropout)       (None, 128)               0         
_________________________________________________________________
dense_3707 (Dense)           (None, 128)               16512     
_________________________________________________________________
dropout_2172 (Dropout)       (None, 128)               0         
__________

13760/13760 [==============================] - 9s 640us/step - loss: 2.0913e-05 - acc: 0.8965 - precision: 0.7837 - recall: 0.9229 - f_one: 0.8466 - val_loss: 2.3771e-05 - val_acc: 0.8823 - val_precision: 0.7624 - val_recall: 0.9015 - val_f_one: 0.8255
Epoch 25/500
13760/13760 [==============================] - 8s 614us/step - loss: 2.0877e-05 - acc: 0.8964 - precision: 0.7836 - recall: 0.9232 - f_one: 0.8465 - val_loss: 2.3846e-05 - val_acc: 0.8561 - val_precision: 0.7345 - val_recall: 0.9331 - val_f_one: 0.8212
Epoch 26/500
13760/13760 [==============================] - 9s 629us/step - loss: 2.0592e-05 - acc: 0.8980 - precision: 0.7873 - recall: 0.9241 - f_one: 0.8489 - val_loss: 2.3647e-05 - val_acc: 0.8858 - val_precision: 0.7779 - val_recall: 0.9081 - val_f_one: 0.8373
Epoch 27/500
13760/13760 [==============================] - 9s 643us/step - loss: 2.0534e-05 - acc: 0.8988 - precision: 0.7891 - recall: 0.9261 - f_one: 0.8505 - val_loss: 2.3758e-05 - val_acc: 0.8753 - val_precisio

/home3/mbrock/anaconda3/envs/tf/lib/python3.7/site-packages/ipykernel_launcher.py:58: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_769 (InputLayer)       (None, 312)               0         
_________________________________________________________________
dense_3712 (Dense)           (None, 2048)              641024    
_________________________________________________________________
dropout_2175 (Dropout)       (None, 2048)              0         
_________________________________________________________________
dense_3713 (Dense)           (None, 2048)              4196352   
_________________________________________________________________
dropout_2176 (Dropout)       (None, 2048)              0         
_________________________________________________________________
dense_3714 (Dense)           (None, 1)                 2049      
Total params: 4,839,425
Trainable params: 4,839,425
Non-trainable params: 0
_________________________________________________________________
